In [1]:
from __future__ import print_function
import os,sys
import chart_studio.plotly as py
import plotly.graph_objects as go
import numpy as np
from readparquet import UBParquetReader
from detectoroutline import DetectorOutline

In [2]:
import lardly
detdata = lardly.DetectorOutline()

Welcome to JupyROOT 6.24/04


In [3]:
# load utility to draw TPC outline
detdata = DetectorOutline()

# define some colors for particle types
ssnet_color_array = np.array( ((0,0,0),      # bg
                               (255,0,0),    # electron
                               (0,255,0),    # gamma
                               (0,0,255),    # muon
                               (255,0,255),  # pion
                               (0,255,255),  # proton
                               (0,0,0)),     # other
                               dtype=np.float ) 

larcvpid2class = {0:0,#unknown -> bg
                  1:0,#cosmic -> bg
                  2:0,#bnb -> bg
                  3:1,#eminus->electron
                  4:2,#gamma->gamma
                  5:2,#pizero->gamma
                  6:3,#muon->muon
                  7:4,#kaon->other
                  8:4,#pion->pion
                  9:5,#proton->proton
                 }

In [4]:
# DATA FILES

# specify location where parquet file(s) live
datafolder="./data/"

reader = UBParquetReader(datafolder)
NENTRIES = reader.nentries

columns:  ['spacepoint_t', 'spacepoint_t_shape', 'imgcoord_t', 'imgcoord_t_shape', 'instance_t', 'instance_t_shape', 'segment_t', 'segment_t_shape', 'truetriplet_t', 'truetriplet_t_shape', 'kplabel_t', 'kplabel_t_shape', 'origin_t', 'origin_t_shape', 'voxcoord', 'voxcoord_shape', 'voxfeat', 'voxfeat_shape', 'voxlabel', 'voxlabel_shape', 'voxkplabel', 'voxkplabel_shape', 'voxssnet', 'voxssnet_shape', 'voxinstance', 'voxinstance_shape', 'voxorigin', 'voxorigin_shape', 'voxoriginweight', 'voxoriginweight_shape', 'run', 'subrun', 'event', 'truepos', 'nu_energy', 'nu_pid', 'nu_ccnc', 'nu_interaction', 'nu_geniemode', 'primary_mom', 'primary_pid', 'primary_start', 'primary_trackid', 'voxinstancelist', 'voxidlist']
nrows:  5


In [12]:
# Get entry data
ENTRY = 3
data = reader.get_entry(ENTRY)

In [13]:
# Print Entry Info
for col in ['run','subrun','event','truepos','nu_energy','nu_pid','nu_ccnc','nu_interaction','nu_geniemode']:
    print(col,": ",data[col])

# make instance 2 id map
instance2id = {}
for k,i in zip(data['voxinstancelist'],data['voxidlist']):
    instance2id[k.as_py()] = i.as_py()
for primdata in zip(data['primary_trackid'].as_py(),data['primary_pid'].as_py(),data['primary_start'].as_py(),data['primary_mom'].as_py()):
    trackid=primdata[0]
    if trackid in instance2id:
        print('[%d]'%(instance2id[primdata[0]]),": ",primdata)
    
#print(instance2id)

run :  1
subrun :  1
event :  4
truepos :  [208.09584045410156, -76.84776306152344, 68.26200103759766]
nu_energy :  1283.047607421875
nu_pid :  12
nu_ccnc :  0
nu_interaction :  1003
nu_geniemode :  1
[267] :  (1249504, 2212, [208.0958494468443, -76.84776493415205, 68.26200020129562], [1063.1461019947933, -353.5818588259185, 50.84100288472131, 349.74320456576316])
[276] :  (1249505, 211, [208.09584944684485, -76.84776493415275, 68.26200020129545], [385.2463264412677, -139.87082957683828, -128.2205114818811, 304.84514514919255])
[270] :  (1249513, 2212, [203.44345564564586, -81.09505438906653, 79.24021433095817], [974.2931451134652, -253.47148023655305, -11.624369731624622, 67.15535223068784])
[275] :  (1249514, 2212, [203.44345564564586, -81.09505438906653, 79.24021433095817], [954.1204375190896, 150.5962142646671, 85.50040169125545, 1.3795745633527425])
[274] :  (1249515, 2212, [203.44345564564586, -81.09505438906653, 79.24021433095817], [947.672216026004, 99.2791088036023, 8.52783167

In [14]:
# GENERATE PLOTLY OBJECTS FOR VISUALIZATION
plotdata = []
nvoxels = data["voxcoord"].shape[0]
# We need to retrieved the 3d positions
pos3d = data["voxcoord"].astype(np.float)*1.0
pos3d[:,1] -= 117.0 


In [15]:
# Plot Particle ID (semenatic segmentation network, "SSNet") labels
no_ghost_points = True

ssnetlabels = data["voxssnet"]
unique_labels = np.unique(ssnetlabels)
print('unique labels: ',unique_labels)
color = np.zeros( (pos3d.shape[0],3), dtype=np.float )
for i in range(7):
   color[ ssnetlabels==i ] = ssnet_color_array[ i,:]

print("ssnetlabels: ",ssnetlabels.shape)
ssnetcol = np.zeros((nvoxels,3))
for i in range(6):
   ssnetcol[ ssnetlabels==i ] = ssnet_color_array[i,:]

if no_ghost_points:
    pos = pos3d[data['voxlabel']==1]
    ssnetcol = ssnetcol[data['voxlabel']==1]
    print("removed ghost voxels: ",pos3d.shape)
else:
    pos = pos3d


ssnetplot = {
    "type":"scatter3d",
    "x":pos[:,0],
    "y":pos[:,1],
    "z":pos[:,2],
        "mode":"markers",
        "name":"ssnet",
        "marker":{"color":ssnetcol,"size":1}
    }

detlines = detdata.getlines(color=(10,10,10))

# DATA
ssnet_plot_data = [ssnetplot] + detdata.getlines(color=(10,10,10))

# LAYOUT
axis_template = {
    "showbackground": True,
    "backgroundcolor": "rgba(100, 100, 100,0.5)",
    "gridcolor": "rgb(50, 50, 50)",
    "zerolinecolor": "rgb(0, 0, 0)",
}


layout = go.Layout(
    title='SSNET LABELS',
    autosize=True,
    hovermode='closest',
    showlegend=False,
    scene= {
        "xaxis": axis_template,
        "yaxis": axis_template,
        "zaxis": axis_template,
        "aspectratio": {"x": 1, "y": 1, "z": 3},
        "camera": {"eye": {"x": 1, "y": 1, "z": 1},
                   "up":dict(x=0, y=1, z=0)},
        "annotations": [],
    }
)

fig = go.Figure(data=ssnet_plot_data, layout=layout)
fig.show()

unique labels:  [0 1 2 3 4 5]
ssnetlabels:  (30061,)
removed ghost voxels:  (30061, 3)


In [16]:
# Voxel visualization with KEYPOINT SCORE LABELS
KPTYPE = 0
KPNAMES = {0:"neutrino",
    1:"track starts",
    2:"track ends",
    3:"shower starts",
    4:"michel starts",
    5:"delta starts"}

no_ghost_points = True

labels = data["voxkplabel"]
print("ssnetlabels: ",labels.shape)
kpcol = np.zeros(nvoxels)
for i in range(6):
   kpcol[:] = labels[KPTYPE,:]

if no_ghost_points:
    pos = pos3d[data['voxlabel']==1]
    kpcol = kpcol[data['voxlabel']==1]
    print("removed ghost voxels: ",pos3d.shape)
else:
    pos = pos3d


ssnetplot = {
    "type":"scatter3d",
    "x":pos[:,0],
    "y":pos[:,1],
    "z":pos[:,2],
        "mode":"markers",
        "name":"ssnet",
        "marker":{"color":kpcol,"size":1,'colorscale':'Viridis'}
    }

detlines = detdata.getlines(color=(10,10,10))

# DATA
ssnet_plot_data = [ssnetplot] + detdata.getlines(color=(10,10,10))

# LAYOUT
axis_template = {
    "showbackground": True,
    "backgroundcolor": "rgba(100, 100, 100,0.5)",
    "gridcolor": "rgb(50, 50, 50)",
    "zerolinecolor": "rgb(0, 0, 0)",
}


layout = go.Layout(
    title='KEYPOINT (%s) LABELS'%(KPNAMES[KPTYPE]),
    autosize=True,
    hovermode='closest',
    showlegend=False,
    scene= {
        "xaxis": axis_template,
        "yaxis": axis_template,
        "zaxis": axis_template,
        "aspectratio": {"x": 1, "y": 1, "z": 3},
        "camera": {"eye": {"x": 1, "y": 1, "z": 1},
                   "up":dict(x=0, y=1, z=0)},
        "annotations": [],
    }
)

fig = go.Figure(data=ssnet_plot_data, layout=layout)
fig.show()

ssnetlabels:  (6, 30061)
removed ghost voxels:  (30061, 3)


In [17]:
# Plot Instance labels
no_ghost_points = True

labels = data["voxinstance"]
unique_labels = np.unique(labels)
print('unique labels: ',unique_labels)
color = np.zeros( (pos3d.shape[0],3), dtype=np.float )
for i in unique_labels.tolist():
    if i==0:
        continue # keep bg instance black
    color[ labels==i ] = np.random.rand(3)*255

print("labels: ",labels.shape)

if no_ghost_points:
    pos = pos3d[data['voxlabel']==1]
    color = color[data['voxlabel']==1]
    print("removed ghost voxels: ",pos3d.shape)
else:
    pos = pos3d


plot = {
    "type":"scatter3d",
    "x":pos[:,0],
    "y":pos[:,1],
    "z":pos[:,2],
        "mode":"markers",
        "name":"instance",
        "marker":{"color":color,"size":1}
    }

detlines = detdata.getlines(color=(10,10,10))

# DATA
plot_data = [plot] + detdata.getlines(color=(10,10,10))

# LAYOUT
axis_template = {
    "showbackground": True,
    "backgroundcolor": "rgba(100, 100, 100,0.5)",
    "gridcolor": "rgb(50, 50, 50)",
    "zerolinecolor": "rgb(0, 0, 0)",
}


layout = go.Layout(
    title='INSTANCE LABELS',
    autosize=True,
    hovermode='closest',
    showlegend=False,
    scene= {
        "xaxis": axis_template,
        "yaxis": axis_template,
        "zaxis": axis_template,
        "aspectratio": {"x": 1, "y": 1, "z": 3},
        "camera": {"eye": {"x": 1, "y": 1, "z": 1},
                   "up":dict(x=0, y=1, z=0)},
        "annotations": [],
    }
)

fig = go.Figure(data=plot_data, layout=layout)
fig.show()

unique labels:  [  0   1   2   3   4   5   7   8   9  12  13  15  16  18  19  20  21  22
  26  27  28  31  32  37  38  41  42  44  45  47  49  50  51  55  56  57
  59  60  61  62  63  64  65  67  69  70  73  75  79  80  81  82  85  88
  90  92  93  94  95  96  97  98  99 100 101 102 104 105 107 109 110 111
 112 115 116 118 122 123 124 126 128 129 130 131 135 137 138 139 140 142
 143 146 147 149 150 151 153 156 157 158 159 160 161 162 166 167 169 170
 171 172 173 174 176 177 178 180 181 182 183 184 186 187 190 192 193 194
 195 196 198 200 201 204 208 209 211 212 213 214 219 222 223 224 225 227
 228 229 230 231 232 234 235 236 237 238 239 241 242 243 244 245 247 248
 249 250 251 253 254 255 256 257 259 264 265 266 267 268 269 270 271 273
 275 276 278 279 280 282 283 284 286 289 291 292 296 298 300 303 304 305
 306 310 316 317 319 331 333 337 345 346 363 371 372]
labels:  (30061,)
removed ghost voxels:  (30061, 3)


In [18]:
# Plot Origin labels
no_ghost_points = True

labels = data["voxorigin"]
unique_labels = np.unique(labels)
print('unique labels: ',unique_labels)
unique_weights = np.unique(data['voxoriginweight'])
print('unique weights: ',unique_weights)

if no_ghost_points:
    pos = pos3d[data['voxlabel']==1]
    color = labels[data['voxlabel']==1]
    print("removed ghost voxels: ",pos3d.shape)
else:
    pos = pos3d
    color = labels


plot = {
    "type":"scatter3d",
    "x":pos[:,0],
    "y":pos[:,1],
    "z":pos[:,2],
        "mode":"markers",
        "name":"origin",
        "marker":{"color":color,"size":1,"colorscale":'Viridis'}
    }

detlines = detdata.getlines(color=(10,10,10))

# DATA
plot_data = [plot] + detdata.getlines(color=(10,10,10))

# LAYOUT
axis_template = {
    "showbackground": True,
    "backgroundcolor": "rgba(100, 100, 100,0.5)",
    "gridcolor": "rgb(50, 50, 50)",
    "zerolinecolor": "rgb(0, 0, 0)",
}


layout = go.Layout(
    title='ORIGIN LABELS',
    autosize=True,
    hovermode='closest',
    showlegend=False,
    scene= {
        "xaxis": axis_template,
        "yaxis": axis_template,
        "zaxis": axis_template,
        "aspectratio": {"x": 1, "y": 1, "z": 3},
        "camera": {"eye": {"x": 1, "y": 1, "z": 1},
                   "up":dict(x=0, y=1, z=0)},
        "annotations": [],
    }
)

fig = go.Figure(data=plot_data, layout=layout)
fig.show()

unique labels:  [0 1]
unique weights:  [1.70230160e-05 7.25689402e-04]
removed ghost voxels:  (30061, 3)
